In [1]:
from modelseedpy.biochem import from_local

# msdb = from_local("/Users/afreiburger/Documents/ModelSEEDDatabase")
msdb = from_local(r"C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase")

modelseedpy 0.2.2


In [2]:
from json import load, dump
from glob import glob

MSDB_json = {}
for jsonData in glob(r"C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_*.json"):
    print(jsonData)
    with open(jsonData, "r") as jsonIn:
        iteration = load(jsonIn)
        iteration_dic = {}
        for rxnInfo in iteration:
            iteration_dic.update({rxnInfo["id"]: rxnInfo})
        MSDB_json.update(iteration_dic)

C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_00.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_01.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_02.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_03.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_04.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_05.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_06.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_07.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\reaction_08.json
C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\

In [3]:
# sorted(list(MSDB_json.keys()))
print(len(MSDB_json.keys()))

56009


In [4]:
from numpy import nan
import re

thermo_values = {}
for file in glob(r"C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase\Biochemistry\Thermodynamics\dGPredictor\json_files\*.json"):
    with open(file, "r") as jsonIn:
        iteration = load(jsonIn)
        rxnJson = {}
        # display(iteration)
        for k,v in iteration.items():
            if isinstance(v, str):  print(f"no dG for {k}") ; continue
            sub_dic_abbrev = MSDB_json[k]["abbreviation"]
            if MSDB_json[k]["abbreviation"] not in v:
                print(k, MSDB_json[k]["abbreviation"], v)
                rxnNum = int(k[3:])
                increase = 1
                sub_dic_abbrev = f"R{rxnNum+increase:05}"
                while sub_dic_abbrev not in v:
                    increase += 1
                    sub_dic_abbrev = f"R{increase:05}"
                    if increase >= 1e6:  print(f"The {k} reaction has not been processed") ; sub_dic_abbrev = None ; break
            if not sub_dic_abbrev:  continue
            if isinstance(v[sub_dic_abbrev], str):  print(f"no dG for {k}") ; continue
            parsed_num = re.sub("([0-9\.\-])", "", str(v[sub_dic_abbrev]["dG_mean"]))
            if parsed_num != "":  print(parsed_num, f"no dG for {k}", v) ; continue
            rxnJson.update({k: v[sub_dic_abbrev]})    
        thermo_values.update(rxnJson)

no dG for rxn00013
no dG for rxn00014
rxn00019 2NPDO {'R00024': {'dG_mean': -36.09110678486431, 'dG_uncer': 0.1531422933954736}}
no dG for rxn00023
no dG for rxn00027
rxn00032 Choline:oxygen 1-oxidoreductase {'R00039': {'dG_mean': 9.89603019707367, 'dG_uncer': 1.2531104413742675}}
rxn00037 R_R00047_c {'R00045': {'dG_mean': -620.0310043183184, 'dG_uncer': 5.776648052959535}}
no dG for rxn00047
rxn00050 rxn00050 {'R00066': {'dG_mean': 58.839374670830736, 'dG_uncer': 6.516833818782413}}
rxn00053 Prostaglandin H2:oxygen oxidoreductase {'R00072': {'dG_mean': -145.56933011998268, 'dG_uncer': 0.7049128338919903}}
nan no dG for rxn00056 {'R00078': {'dG_mean': nan, 'dG_uncer': nan}}
no dG for rxn00058
no dG for rxn00059
nan no dG for rxn00068 {'R00092': {'dG_mean': nan, 'dG_uncer': nan}}
rxn00073 rxn00073 {'R00097': {'dG_mean': 382.20282752091407, 'dG_uncer': 0.1109804195398385}}
rxn00075 NADNm {'R00102': {'dG_mean': -18.099300482432312, 'dG_uncer': 1.031583345874511}}
nan no dG for rxn00079 {'

In [5]:
sorted(list(thermo_values.keys()))
print(len(thermo_values.keys()))

27694


In [6]:
from scipy.constants import calorie
for rxnID, content in MSDB_json.items():
    if "deltag" not in MSDB_json[rxnID]:  continue
    parsed_num = re.sub("([0-9\.\-])", "", str(MSDB_json[rxnID]["deltag"]))
    if rxnID not in thermo_values and parsed_num == "":
        MSDB_json[rxnID]["deltag"] = float(MSDB_json[rxnID]["deltag"])
        MSDB_json[rxnID]["deltagerr"] = float(MSDB_json[rxnID]["deltagerr"])
        MSDB_json[rxnID]["deltag"] *= calorie
        MSDB_json[rxnID]["deltagerr"] *= calorie
        continue
    print(rxnID, thermo_values[rxnID])
    MSDB_json[rxnID]["deltag"] = thermo_values[rxnID]["dG_mean"]
    MSDB_json[rxnID]["deltagerr"] = thermo_values[rxnID]["dG_uncer"]

rxn00001 {'dG_mean': -15.978962709842271, 'dG_uncer': 0.1018229252895586}
rxn00002 {'dG_mean': -96.33065567460018, 'dG_uncer': 1.0434631147207318}
rxn00003 {'dG_mean': 23.87794947248591, 'dG_uncer': 1.4856033440752583}
rxn00004 {'dG_mean': -6.199860585711548, 'dG_uncer': 1.4639140224940748}
rxn00006 {'dG_mean': -194.716885616239, 'dG_uncer': 0.25372185665117}
rxn00007 {'dG_mean': -12.452251693186184, 'dG_uncer': 0.1081426968520035}
rxn00008 {'dG_mean': -270.65162982126355, 'dG_uncer': 2.918353088339725}
rxn00009 {'dG_mean': 1.758495360068423, 'dG_uncer': 0.1146015302373187}
rxn00010 {'dG_mean': -21.611593067013388, 'dG_uncer': 0.1800158687929662}
rxn00011 {'dG_mean': -30.62003175875685, 'dG_uncer': 1.81908017782148}
rxn00012 {'dG_mean': -21.438871437328714, 'dG_uncer': 1.509286832755146}
rxn00015 {'dG_mean': -19.23769046955533, 'dG_uncer': 2.341528284748625}
rxn00016 {'dG_mean': 10.518926978742796, 'dG_uncer': 1.389158150064834}
rxn00017 {'dG_mean': -18.62173462650817, 'dG_uncer': 2.85

In [7]:
print(MSDB_json["rxn00014"]["deltag"])
from numpy import array_split

# export JSON processing
MSDB_lists = array_split(list(MSDB_json.values()), 61)

41840000.0


In [9]:
for index, portion in enumerate(MSDB_lists):
    with open(f"reaction_{index:02}.json", "w") as jsonOut:
        dump(list(portion), jsonOut, indent=3)

In [36]:
msdb = from_local(r"C:\Users\Andrew Freiburger\Documents\Argonne\ModelSEED\ModelSEEDDatabase")

In [8]:
print(msdb.reactions.rxn00001.delta_g)

-3.46
